# Práctica 3: Inteligencia Artificial. FIFA
> #### Pedro Font Antón 

El objeto principal del problema es, a partir de la base de datos de jugadores de FIFA, calcular la valoración económica de un jugador, el cual está intrínsicamente relacionado con sus respectivas características. Por tanto, lo que queremos es predecir el *valor* de los jugadores usando la información del jugador. Para ello haremos una limpieza de los datos, y ajustaremos los parámetros del algoritmo de aprendizaje automático.

## Importamos librerias

Primero, importamos las librerias que vamos a utilizar.

In [1]:
import os

from sklearn.model_selection import train_test_split
from sklearn import linear_model
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score

import pandas as pd
import numpy as np


## Leer los datos

Para hacer la lectura de los datos vamos a usar ``pandas`` y una utilidad de la libreria, llamada
``os``.


In [2]:
df = pd.read_csv(os.path.join("in", "fifa.csv"))
df.head()

Unnamed: 0      ID               Name  Age  \
0           0  158023           L. Messi   31   
1           1   20801  Cristiano Ronaldo   33   
2           2  190871          Neymar Jr   26   
3           3  193080             De Gea   27   
4           4  192985       K. De Bruyne   27   

                                            Photo Nationality  \
0  https://cdn.sofifa.org/players/4/19/158023.png   Argentina   
1   https://cdn.sofifa.org/players/4/19/20801.png    Portugal   
2  https://cdn.sofifa.org/players/4/19/190871.png      Brazil   
3  https://cdn.sofifa.org/players/4/19/193080.png       Spain   
4  https://cdn.sofifa.org/players/4/19/192985.png     Belgium   

                                  Flag  Overall  Potential  \
0  https://cdn.sofifa.org/flags/52.png       94         94   
1  https://cdn.sofifa.org/flags/38.png       94         94   
2  https://cdn.sofifa.org/flags/54.png       92         93   
3  https://cdn.sofifa.org/flags/45.png       91         93   
4   https://cdn.sofifa.org/flags/7.png       91         92   

                  Club  ... Composure Marking StandingTackle  SlidingTackle  \
0         FC Barcelona  ...      96.0    33.0           28.0           26.0   
1             Juventus  ...      95.0    28.0           31.0           23.0   
2  Paris Saint-Germain  ...      94.0    27.0           24.0           33.0   
3    Manchester United  ...      68.0    15.0           21.0           13.0   
4      Manchester City  ...      88.0    68.0           58.0           51.0   

  GKDiving  GKHandling  GKKicking  GKPositioning GKReflexes Release Clause  
0      6.0        11.0       15.0           14.0        8.0        €226.5M  
1      7.0        11.0       15.0           14.0       11.0        €127.1M  
2      9.0         9.0       15.0           15.0       11.0        €228.1M  
3     90.0        85.0       87.0           88.0       94.0        €138.6M  
4     15.0        13.0        5.0           10.0       13.0        €196.4M  

[5 rows x 89 columns]

Una vez hecho esto, ya tendremos nuestra base de datos con todos los jugadores de FIFA 18 cargada.

# Análisis de los datos
Primero de todo, queremos saber que sucede con los datos. Para hacerlo, **incrementaré** el número de columnas que se visualizan.
Tras ello, usaré una instrucción especial que nos mostrará la **estructura de los datos**.

In [3]:
#Comando para ver todas las columnas 
pd.set_option('display.max_columns', None)
df

Unnamed: 0      ID                Name  Age  \
0               0  158023            L. Messi   31   
1               1   20801   Cristiano Ronaldo   33   
2               2  190871           Neymar Jr   26   
3               3  193080              De Gea   27   
4               4  192985        K. De Bruyne   27   
...           ...     ...                 ...  ...   
18202       18202  238813        J. Lundstram   19   
18203       18203  243165  N. Christoffersson   19   
18204       18204  241638           B. Worman   16   
18205       18205  246268      D. Walker-Rice   17   
18206       18206  246269           G. Nugent   16   

                                                Photo Nationality  \
0      https://cdn.sofifa.org/players/4/19/158023.png   Argentina   
1       https://cdn.sofifa.org/players/4/19/20801.png    Portugal   
2      https://cdn.sofifa.org/players/4/19/190871.png      Brazil   
3      https://cdn.sofifa.org/players/4/19/193080.png       Spain   
4      https://cdn.sofifa.org/players/4/19/192985.png     Belgium   
...                                               ...         ...   
18202  https://cdn.sofifa.org/players/4/19/238813.png     England   
18203  https://cdn.sofifa.org/players/4/19/243165.png      Sweden   
18204  https://cdn.sofifa.org/players/4/19/241638.png     England   
18205  https://cdn.sofifa.org/players/4/19/246268.png     England   
18206  https://cdn.sofifa.org/players/4/19/246269.png     England   

                                      Flag  Overall  Potential  \
0      https://cdn.sofifa.org/flags/52.png       94         94   
1      https://cdn.sofifa.org/flags/38.png       94         94   
2      https://cdn.sofifa.org/flags/54.png       92         93   
3      https://cdn.sofifa.org/flags/45.png       91         93   
4       https://cdn.sofifa.org/flags/7.png       91         92   
...                                    ...      ...        ...   
18202  https://cdn.sofifa.org/flags/14.png       47         65   
18203  https://cdn.sofifa.org/flags/46.png       47         63   
18204  https://cdn.sofifa.org/flags/14.png       47         67   
18205  https://cdn.sofifa.org/flags/14.png       47         66   
18206  https://cdn.sofifa.org/flags/14.png       46         66   

                      Club                                       Club Logo  \
0             FC Barcelona    https://cdn.sofifa.org/teams/2/light/241.png   
1                 Juventus     https://cdn.sofifa.org/teams/2/light/45.png   
2      Paris Saint-Germain     https://cdn.sofifa.org/teams/2/light/73.png   
3        Manchester United     https://cdn.sofifa.org/teams/2/light/11.png   
4          Manchester City     https://cdn.sofifa.org/teams/2/light/10.png   
...                    ...                                             ...   
18202      Crewe Alexandra    https://cdn.sofifa.org/teams/2/light/121.png   
18203       Trelleborgs FF    https://cdn.sofifa.org/teams/2/light/703.png   
18204     Cambridge United   https://cdn.sofifa.org/teams/2/light/1944.png   
18205      Tranmere Rovers  https://cdn.sofifa.org/teams/2/light/15048.png   
18206      Tranmere Rovers  https://cdn.sofifa.org/teams/2/light/15048.png   

         Value   Wage  Special Preferred Foot  International Reputation  \
0      €110.5M  €565K     2202           Left                       5.0   
1         €77M  €405K     2228          Right                       5.0   
2      €118.5M  €290K     2143          Right                       5.0   
3         €72M  €260K     1471          Right                       4.0   
4        €102M  €355K     2281          Right                       4.0   
...        ...    ...      ...            ...                       ...   
18202     €60K    €1K     1307          Right                       1.0   
18203     €60K    €1K     1098          Right                       1.0   
18204     €60K    €1K     1189          Right                       1.0   
18205     €60K    €1K     1228          Right    

Después de ejecutar la instrucción anterior, vemos que nos salen ya todas las columnas. Ahora, podemos observar que
las dos primeras columnas no nos dan información significativa, así que las voy a eliminar.

In [4]:
df = df.iloc[:, 2:]
df

Name  Age  \
0                L. Messi   31   
1       Cristiano Ronaldo   33   
2               Neymar Jr   26   
3                  De Gea   27   
4            K. De Bruyne   27   
...                   ...  ...   
18202        J. Lundstram   19   
18203  N. Christoffersson   19   
18204           B. Worman   16   
18205      D. Walker-Rice   17   
18206           G. Nugent   16   

                                                Photo Nationality  \
0      https://cdn.sofifa.org/players/4/19/158023.png   Argentina   
1       https://cdn.sofifa.org/players/4/19/20801.png    Portugal   
2      https://cdn.sofifa.org/players/4/19/190871.png      Brazil   
3      https://cdn.sofifa.org/players/4/19/193080.png       Spain   
4      https://cdn.sofifa.org/players/4/19/192985.png     Belgium   
...                                               ...         ...   
18202  https://cdn.sofifa.org/players/4/19/238813.png     England   
18203  https://cdn.sofifa.org/players/4/19/243165.png      Sweden   
18204  https://cdn.sofifa.org/players/4/19/241638.png     England   
18205  https://cdn.sofifa.org/players/4/19/246268.png     England   
18206  https://cdn.sofifa.org/players/4/19/246269.png     England   

                                      Flag  Overall  Potential  \
0      https://cdn.sofifa.org/flags/52.png       94         94   
1      https://cdn.sofifa.org/flags/38.png       94         94   
2      https://cdn.sofifa.org/flags/54.png       92         93   
3      https://cdn.sofifa.org/flags/45.png       91         93   
4       https://cdn.sofifa.org/flags/7.png       91         92   
...                                    ...      ...        ...   
18202  https://cdn.sofifa.org/flags/14.png       47         65   
18203  https://cdn.sofifa.org/flags/46.png       47         63   
18204  https://cdn.sofifa.org/flags/14.png       47         67   
18205  https://cdn.sofifa.org/flags/14.png       47         66   
18206  https://cdn.sofifa.org/flags/14.png       46         66   

                      Club                                       Club Logo  \
0             FC Barcelona    https://cdn.sofifa.org/teams/2/light/241.png   
1                 Juventus     https://cdn.sofifa.org/teams/2/light/45.png   
2      Paris Saint-Germain     https://cdn.sofifa.org/teams/2/light/73.png   
3        Manchester United     https://cdn.sofifa.org/teams/2/light/11.png   
4          Manchester City     https://cdn.sofifa.org/teams/2/light/10.png   
...                    ...                                             ...   
18202      Crewe Alexandra    https://cdn.sofifa.org/teams/2/light/121.png   
18203       Trelleborgs FF    https://cdn.sofifa.org/teams/2/light/703.png   
18204     Cambridge United   https://cdn.sofifa.org/teams/2/light/1944.png   
18205      Tranmere Rovers  https://cdn.sofifa.org/teams/2/light/15048.png   
18206      Tranmere Rovers  https://cdn.sofifa.org/teams/2/light/15048.png   

         Value   Wage  Special Preferred Foot  International Reputation  \
0      €110.5M  €565K     2202           Left                       5.0   
1         €77M  €405K     2228          Right                       5.0   
2      €118.5M  €290K     2143          Right                       5.0   
3         €72M  €260K     1471          Right                       4.0   
4        €102M  €355K     2281          Right                       4.0   
...        ...    ...      ...            ...                       ...   
18202     €60K    €1K     1307          Right                       1.0   
18203     €60K    €1K     1098          Right                       1.0   
18204     €60K    €1K     1189          Right                       1.0   
18205     €60K    €1K     1228          Right                       1.0   
18206     €60K    €1K     1321          Right                       1.0   

       Weak Foot  Skill Moves       Work Rate   Body Type Real Face Position  \
0            4.0          4.0  Medium/ Medium       Messi       Yes     

Tras analizar cada columna y los valores que contiene, decido eliminar las columnas: **foto, bandera, logo del club, dorsal, 'real face' y nombre** ya que no tienen tampoco valores útiles a la hora de entrenar el algoritmo. Básicamente la foto, el logo (escudi) y bandera son archivos .png que son simplemente para visualizar las imagenes en el juego. El dorsal, el nombre y si tienen hecha la cara real dentro del juego, claramente no afectaran tampoco al precio. En definitiva, eliminamos simplemente elementos que solo sirven a nivel estético dentro del juego.

Lo haremos con la siguiente instrucción:

In [5]:
df.drop(['Photo','Flag','Club Logo','Jersey Number','Real Face','Name'], axis = 1,inplace=True)
df

Age Nationality  Overall  Potential                 Club    Value  \
0       31   Argentina       94         94         FC Barcelona  €110.5M   
1       33    Portugal       94         94             Juventus     €77M   
2       26      Brazil       92         93  Paris Saint-Germain  €118.5M   
3       27       Spain       91         93    Manchester United     €72M   
4       27     Belgium       91         92      Manchester City    €102M   
...    ...         ...      ...        ...                  ...      ...   
18202   19     England       47         65      Crewe Alexandra     €60K   
18203   19      Sweden       47         63       Trelleborgs FF     €60K   
18204   16     England       47         67     Cambridge United     €60K   
18205   17     England       47         66      Tranmere Rovers     €60K   
18206   16     England       46         66      Tranmere Rovers     €60K   

        Wage  Special Preferred Foot  International Reputation  Weak Foot  \
0      €565K     2202           Left                       5.0        4.0   
1      €405K     2228          Right                       5.0        4.0   
2      €290K     2143          Right                       5.0        5.0   
3      €260K     1471          Right                       4.0        3.0   
4      €355K     2281          Right                       4.0        5.0   
...      ...      ...            ...                       ...        ...   
18202    €1K     1307          Right                       1.0        2.0   
18203    €1K     1098          Right                       1.0        2.0   
18204    €1K     1189          Right                       1.0        3.0   
18205    €1K     1228          Right                       1.0        3.0   
18206    €1K     1321          Right                       1.0        3.0   

       Skill Moves       Work Rate   Body Type Position        Joined  \
0              4.0  Medium/ Medium       Messi       RF   Jul 1, 2004   
1              5.0       High/ Low  C. Ronaldo       ST  Jul 10, 2018   
2              5.0    High/ Medium      Neymar       LW   Aug 3, 2017   
3              1.0  Medium/ Medium        Lean       GK   Jul 1, 2011   
4              4.0      High/ High      Normal      RCM  Aug 30, 2015   
...            ...             ...         ...      ...           ...   
18202          2.0  Medium/ Medium        Lean       CM   May 3, 2017   
18203          2.0  Medium/ Medium      Normal       ST  Mar 19, 2018   
18204          2.0  Medium/ Medium      Normal       ST   Jul 1, 2017   
18205          2.0  Medium/ Medium        Lean       RW  Apr 24, 2018   
18206          2.0  Medium/ Medium        Lean       CM  Oct 30, 2018   

      Loaned From Contract Valid Until Height  Weight    LS    ST    RS    LW  \
0             NaN                 2021    5'7  159lbs  88+2  88+2  88+2  92+2   
1             NaN                 2022    6'2  183lbs  91+3  91+3  91+3  89+3   
2             NaN                 2022    5'9  150lbs  84+3  84+3  84+3  89+3   
3             NaN                 2020    6'4  168lbs   NaN   NaN   NaN   NaN   
4             NaN                 2023   5'11  154lbs  82+3  82+3  82+3  87+3   
...           ...                  ...    ...     ...   ...   ...   ...   ...   
18202         NaN                 2019    5'9  134lbs  42+2  42+2  42+2  44+2   
18203         NaN                 2020    6'3  170lbs  45+2  45+2  45+2  39+2   
18204         NaN                 2021    5'8  148lbs  45+2  45+2  45+2  45+2   
18205         NaN                 2019   5'10  154lbs  47+2  47+2  47+2  47+2   
18206         NaN                 2019   5'10  176lbs  43+2  43+2  43+2  45+2   

         LF    CF    RF    RW   LAM   CAM   RAM    LM   LCM    CM   RCM    RM  \
0      93+2  93+2  93+2  92+2  93+2  93+2  93+2  91+2  84+2  84+2  84+2  91+2   
1      90+3  90+3  90+3  89+3  88+3  88+3  88+3  88+3  81+3  81+3  81+3  88+3   
2      89+3  89+3  89+3  89+3  89+3  89+3  89+3  88+3  81+3  81+3  81+3  88+

Una vez elimindas las columnas, el primer problema que me encuentro, es que hay columnas que contienen **valores monetarios**, los cuales están en **euros**. También contienen **'K' o 'M'** según sean **miles o millones** de euros. Esto será un problema ya que nos interesa que todos los valores numéricos sean float.
>Para solucionarlo, crearemos una función para pasar esos valores a float, sin símbolos extra.

In [6]:
def value_to_float(x):
    """
    From K and M to float.
    
    """
    x = x.replace('€', '')
    ret_val = 0.0
    
    if type(x) == float or type(x) == int:
        ret_val = x
    if 'K' in x:
        if len(x) > 1:
            ret_val = float(x.replace('K', ''))
        ret_val = ret_val *1000
    if 'M' in x:
        if len(x) > 1:
            ret_val = float(x.replace('M', ''))
        ret_val = ret_val * 1000000.0
    return ret_val

Una vez guardada la función, intenté aplicarla en las tres columnas que lo necesitan, ya que contienen cifras en miles o millones de euros. Estas columnas son las siguientes: **Value, Wage y Release Clause**.
Lo intenté ejecutar de primeras en las 3, pero vemos que en la última detectó NaNs.
> Lo vemos en la última columna de la siguiente ejecución:

In [7]:
df.loc[df['Release Clause'].isnull()]

Age Nationality  Overall  Potential                            Club  \
28      26    Colombia       88         89               FC Bayern München   
38      30   Argentina       88         88                           Milan   
91      29      Brazil       85         85  Guangzhou Evergrande Taobao FC   
166     24      Brazil       83         90  Guangzhou Evergrande Taobao FC   
176     24     Croatia       83         89                         Chelsea   
...    ...         ...      ...        ...                             ...   
17979   21    China PR       51         60             Guizhou Hengfeng FC   
18026   21    China PR       50         59             Guizhou Hengfeng FC   
18031   20    China PR       50         61                  Stabæk Fotball   
18056   19       Italy       50         65                          Ascoli   
18183   44     England       48         48                Cambridge United   

        Value   Wage  Special Preferred Foot  International Reputation  \
28     €69.5M  €315K     2171           Left                       4.0   
38       €57M  €245K     1965          Right                       4.0   
91       €37M  €235K     2245          Right                       3.0   
166    €36.5M   €18K     2142           Left                       2.0   
176      €35M  €165K     2115          Right                       3.0   
...       ...    ...      ...            ...                       ...   
17979    €60K    €2K     1459          Right                       1.0   
18026    €50K    €2K     1440          Right                       1.0   
18031    €40K    €2K     1278          Right                       1.0   
18056    €60K    €3K     1450           Left                       1.0   
18183      €0    €1K      774          Right                       1.0   

       Weak Foot  Skill Moves       Work Rate Body Type Position  \
28           3.0          4.0  Medium/ Medium    Normal      LAM   
38           4.0          3.0    High/ Medium    Normal       LS   
91           3.0          3.0      High/ High      Lean      LDM   
166          4.0          4.0    High/ Medium    Normal      CAM   
176          4.0          4.0      High/ High    Normal      LCM   
...          ...          ...             ...       ...      ...   
17979        2.0          2.0  Medium/ Medium    Normal       CM   
18026        2.0          2.0  Medium/ Medium      Lean       LM   
18031        3.0          2.0  Medium/ Medium    Normal       RB   
18056        3.0          2.0  Medium/ Medium      Lean       CM   
18183        2.0          1.0  Medium/ Medium    Normal       GK   

             Joined              Loaned From Contract Valid Until Height  \
28              NaN              Real Madrid         Jun 30, 2019   5'11   
38              NaN                 Juventus         Jun 30, 2019    6'1   
91              NaN             FC Barcelona         Jun 30, 2019    6'0   
166             NaN               SL Benfica         Dec 31, 2018    6'3   
176             NaN              Real Madrid         Jun 30, 2019    5'9   
...             ...                      ...                  ...    ...   
17979           NaN      Tianjin Quanjian FC         Dec 31, 2018    6'0   
18026           NaN        Jiangsu Suning FC         Dec 31, 2018   5'10   
18031           NaN  Beijing Sinobo Guoan FC         Dec 31, 2018    5'7   
18056           NaN                     Roma         Jun 30, 2019   5'10   
18183  Aug 17, 2018                      NaN                 2023    6'2   

       Weight    LS    ST    RS    LW    LF    CF    RF    RW   LAM   CAM  \
28     172lbs  80+3  80+3  80+3  84+3  83+3  83+3  83+3  84+3  85+3  85+3   
38     196lbs  85+3  85+3  85+3  81+3  83+3  83+3  83+3  81+3  80+3  80+3   
91     157lbs  81+3  81+3  81+3  79+3  81+3  81+3  81+3  79+3  81+3  81+3   
166    176lbs  80+2  80+2  80+2  81+2  81+2  81+2  81+2  81+2  81+2  81+2   
176    172lbs  71+3  71+3  71+3  79+3  78+3  78+3  78+3  79+3  81+

Como podemos observar, hay *1564* jugadores que contienen ``NaN`` en su cláusula de rescisión.
La solución más práctica que se me ha ocurrido es **poner a 0** esos valores, ya que el jugador no dispone de esa clausula de rescisión, entonces es lo que me parece más lógico. 
La segunda instrucción nos servirá para ver la tabla y comprobar si ha funcionado.

>Pongo **0€** y no 0 sin el símbolo de euro, ya que me daba error si lo ponía sin el símbolo de euro al aplicar la funcion value to float en la columna de cláusula de rescisión.

In [8]:
df["Release Clause"].fillna('0€', inplace=True)
df.loc[df['Release Clause'] == '0€']

Age Nationality  Overall  Potential                            Club  \
28      26    Colombia       88         89               FC Bayern München   
38      30   Argentina       88         88                           Milan   
91      29      Brazil       85         85  Guangzhou Evergrande Taobao FC   
166     24      Brazil       83         90  Guangzhou Evergrande Taobao FC   
176     24     Croatia       83         89                         Chelsea   
...    ...         ...      ...        ...                             ...   
17979   21    China PR       51         60             Guizhou Hengfeng FC   
18026   21    China PR       50         59             Guizhou Hengfeng FC   
18031   20    China PR       50         61                  Stabæk Fotball   
18056   19       Italy       50         65                          Ascoli   
18183   44     England       48         48                Cambridge United   

        Value   Wage  Special Preferred Foot  International Reputation  \
28     €69.5M  €315K     2171           Left                       4.0   
38       €57M  €245K     1965          Right                       4.0   
91       €37M  €235K     2245          Right                       3.0   
166    €36.5M   €18K     2142           Left                       2.0   
176      €35M  €165K     2115          Right                       3.0   
...       ...    ...      ...            ...                       ...   
17979    €60K    €2K     1459          Right                       1.0   
18026    €50K    €2K     1440          Right                       1.0   
18031    €40K    €2K     1278          Right                       1.0   
18056    €60K    €3K     1450           Left                       1.0   
18183      €0    €1K      774          Right                       1.0   

       Weak Foot  Skill Moves       Work Rate Body Type Position  \
28           3.0          4.0  Medium/ Medium    Normal      LAM   
38           4.0          3.0    High/ Medium    Normal       LS   
91           3.0          3.0      High/ High      Lean      LDM   
166          4.0          4.0    High/ Medium    Normal      CAM   
176          4.0          4.0      High/ High    Normal      LCM   
...          ...          ...             ...       ...      ...   
17979        2.0          2.0  Medium/ Medium    Normal       CM   
18026        2.0          2.0  Medium/ Medium      Lean       LM   
18031        3.0          2.0  Medium/ Medium    Normal       RB   
18056        3.0          2.0  Medium/ Medium      Lean       CM   
18183        2.0          1.0  Medium/ Medium    Normal       GK   

             Joined              Loaned From Contract Valid Until Height  \
28              NaN              Real Madrid         Jun 30, 2019   5'11   
38              NaN                 Juventus         Jun 30, 2019    6'1   
91              NaN             FC Barcelona         Jun 30, 2019    6'0   
166             NaN               SL Benfica         Dec 31, 2018    6'3   
176             NaN              Real Madrid         Jun 30, 2019    5'9   
...             ...                      ...                  ...    ...   
17979           NaN      Tianjin Quanjian FC         Dec 31, 2018    6'0   
18026           NaN        Jiangsu Suning FC         Dec 31, 2018   5'10   
18031           NaN  Beijing Sinobo Guoan FC         Dec 31, 2018    5'7   
18056           NaN                     Roma         Jun 30, 2019   5'10   
18183  Aug 17, 2018                      NaN                 2023    6'2   

       Weight    LS    ST    RS    LW    LF    CF    RF    RW   LAM   CAM  \
28     172lbs  80+3  80+3  80+3  84+3  83+3  83+3  83+3  84+3  85+3  85+3   
38     196lbs  85+3  85+3  85+3  81+3  83+3  83+3  83+3  81+3  80+3  80+3   
91     157lbs  81+3  81+3  81+3  79+3  81+3  81+3  81+3  79+3  81+3  81+3   
166    176lbs  80+2  80+2  80+2  81+2  81+2  81+2  81+2  81+2  81+2  81+2   
176    172lbs  71+3  71+3  71+3  79+3  78+3  78+3  78+3  79+3  81+

Una vez arreglado el problema de los NaNs en la cláusula de rescisión, aplicamos ahora sí, la función en las siguientes columnas, ya de manera correcta. Acto seguido observamos la tabla para ver si ha ido correctamente.

In [9]:
df["Value"] = df["Value"].apply(value_to_float)
df["Wage"] = df["Wage"].apply(value_to_float)
df["Release Clause"] = df["Release Clause"].apply(value_to_float)
df.head()

Age Nationality  Overall  Potential                 Club        Value  \
0   31   Argentina       94         94         FC Barcelona  110500000.0   
1   33    Portugal       94         94             Juventus   77000000.0   
2   26      Brazil       92         93  Paris Saint-Germain  118500000.0   
3   27       Spain       91         93    Manchester United   72000000.0   
4   27     Belgium       91         92      Manchester City  102000000.0   

       Wage  Special Preferred Foot  International Reputation  Weak Foot  \
0  565000.0     2202           Left                       5.0        4.0   
1  405000.0     2228          Right                       5.0        4.0   
2  290000.0     2143          Right                       5.0        5.0   
3  260000.0     1471          Right                       4.0        3.0   
4  355000.0     2281          Right                       4.0        5.0   

   Skill Moves       Work Rate   Body Type Position        Joined Loaned From  \
0          4.0  Medium/ Medium       Messi       RF   Jul 1, 2004         NaN   
1          5.0       High/ Low  C. Ronaldo       ST  Jul 10, 2018         NaN   
2          5.0    High/ Medium      Neymar       LW   Aug 3, 2017         NaN   
3          1.0  Medium/ Medium        Lean       GK   Jul 1, 2011         NaN   
4          4.0      High/ High      Normal      RCM  Aug 30, 2015         NaN   

  Contract Valid Until Height  Weight    LS    ST    RS    LW    LF    CF  \
0                 2021    5'7  159lbs  88+2  88+2  88+2  92+2  93+2  93+2   
1                 2022    6'2  183lbs  91+3  91+3  91+3  89+3  90+3  90+3   
2                 2022    5'9  150lbs  84+3  84+3  84+3  89+3  89+3  89+3   
3                 2020    6'4  168lbs   NaN   NaN   NaN   NaN   NaN   NaN   
4                 2023   5'11  154lbs  82+3  82+3  82+3  87+3  87+3  87+3   

     RF    RW   LAM   CAM   RAM    LM   LCM    CM   RCM    RM   LWB   LDM  \
0  93+2  92+2  93+2  93+2  93+2  91+2  84+2  84+2  84+2  91+2  64+2  61+2   
1  90+3  89+3  88+3  88+3  88+3  88+3  81+3  81+3  81+3  88+3  65+3  61+3   
2  89+3  89+3  89+3  89+3  89+3  88+3  81+3  81+3  81+3  88+3  65+3  60+3   
3   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
4  87+3  87+3  88+3  88+3  88+3  88+3  87+3  87+3  87+3  88+3  77+3  77+3   

    CDM   RDM   RWB    LB   LCB    CB   RCB    RB  Crossing  Finishing  \
0  61+2  61+2  64+2  59+2  47+2  47+2  47+2  59+2      84.0       95.0   
1  61+3  61+3  65+3  61+3  53+3  53+3  53+3  61+3      84.0       94.0   
2  60+3  60+3  65+3  60+3  47+3  47+3  47+3  60+3      79.0       87.0   
3   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN      17.0       13.0   
4  77+3  77+3  77+3  73+3  66+3  66+3  66+3  73+3      93.0       82.0   

   HeadingAccuracy  ShortPassing  Volleys  Dribbling  Curve  FKAccuracy  \
0             70.0          90.0     86.0       97.0   93.0        94.0   
1             89.0          81.0     87.0       88.0   81.0        76.0   
2             62.0          84.0     84.0       96.0   88.0        87.0   
3             21.0          50.0     13.0       18.0   21.0        19.0   
4             55.0          92.0     82.0       86.0   85.0        83.0   

   LongPassing  BallControl  Acceleration  SprintSpeed  Agility  Reactions  \
0         87.0         96.0          91.0         86.0     91.0       95.0   
1         77.0         94.0          89.0         91.0     87.0       96.0   
2         78.0         95.0          94.0         90.0     96.0       94.0   
3         51.0         42.0          57.0         58.0     60.0       90.0   
4         91.0         91.0          78.0         76.0     79.0       91.0   

   Balance  ShotPower  Jumping  Stamina  Strength  LongShots  Aggression  \
0     95.0       85.0     68.0     72.0      59.0       94.0        48.0   
1     70.0       95.0     95.0     88.0      79.0       93.0        63.0   
2     84.0       80.0     61.0     81.0      49.0       82.0        56.0   
3     4

Vemos que ha ido según lo esperado, las columnas Value, Wage y Release Clause están correctamente pasadas a float, así que continuamos.

## Hot Encoding
A continuación, me encuentro con el siguiente **problema:** hay columnas que no tienen valores **numéricos**, pero su información me **interesa** para el entrenamiento del modelo. Por lo tanto, lo que haré será utilizar la técnica de **hot-encoding**, la cual creará una columna por cada valor que se encuentre en la columna inicial (en la que lo aplicamos), y pondrá un ``1`` en el valor inicial que teníamos, y a todo lo demás un ``0``.
> En este primer momento, lo aplicaré en Nacionalidad, Club, Posición y Pie Hábil.


In [10]:
na = df.pop("Nationality")
df = pd.concat([df.reset_index(drop=True), pd.get_dummies(na, prefix='nat').reset_index(drop=True)],axis=1, sort=False)
filtro_Pos = [col for col in df if col.startswith('nat')]
df.drop(columns=filtro_Pos)

cl = df.pop("Club")
df = pd.concat([df.reset_index(drop=True), pd.get_dummies(cl, prefix='clb').reset_index(drop=True)],axis=1, sort=False)
filtro_Pos = [col for col in df if col.startswith('clb')]
df.drop(columns=filtro_Pos)

po = df.pop("Position")
df = pd.concat([df.reset_index(drop=True), pd.get_dummies(po, prefix='pos').reset_index(drop=True)],axis=1, sort=False)
filtro_Pos = [col for col in df if col.startswith('pos')]
df.drop(columns=filtro_Pos)

pf = df.pop("Preferred Foot")
df = pd.concat([df.reset_index(drop=True), pd.get_dummies(pf, prefix='foot').reset_index(drop=True)],axis=1, sort=False)
filtro_Pos = [col for col in df if col.startswith('foot')]
df.drop(columns=filtro_Pos)

df.head()



Age  Overall  Potential        Value      Wage  Special  \
0   31       94         94  110500000.0  565000.0     2202   
1   33       94         94   77000000.0  405000.0     2228   
2   26       92         93  118500000.0  290000.0     2143   
3   27       91         93   72000000.0  260000.0     1471   
4   27       91         92  102000000.0  355000.0     2281   

   International Reputation  Weak Foot  Skill Moves       Work Rate  \
0                       5.0        4.0          4.0  Medium/ Medium   
1                       5.0        4.0          5.0       High/ Low   
2                       5.0        5.0          5.0    High/ Medium   
3                       4.0        3.0          1.0  Medium/ Medium   
4                       4.0        5.0          4.0      High/ High   

    Body Type        Joined Loaned From Contract Valid Until Height  Weight  \
0       Messi   Jul 1, 2004         NaN                 2021    5'7  159lbs   
1  C. Ronaldo  Jul 10, 2018         NaN                 2022    6'2  183lbs   
2      Neymar   Aug 3, 2017         NaN                 2022    5'9  150lbs   
3        Lean   Jul 1, 2011         NaN                 2020    6'4  168lbs   
4      Normal  Aug 30, 2015         NaN                 2023   5'11  154lbs   

     LS    ST    RS    LW    LF    CF    RF    RW   LAM   CAM   RAM    LM  \
0  88+2  88+2  88+2  92+2  93+2  93+2  93+2  92+2  93+2  93+2  93+2  91+2   
1  91+3  91+3  91+3  89+3  90+3  90+3  90+3  89+3  88+3  88+3  88+3  88+3   
2  84+3  84+3  84+3  89+3  89+3  89+3  89+3  89+3  89+3  89+3  89+3  88+3   
3   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
4  82+3  82+3  82+3  87+3  87+3  87+3  87+3  87+3  88+3  88+3  88+3  88+3   

    LCM    CM   RCM    RM   LWB   LDM   CDM   RDM   RWB    LB   LCB    CB  \
0  84+2  84+2  84+2  91+2  64+2  61+2  61+2  61+2  64+2  59+2  47+2  47+2   
1  81+3  81+3  81+3  88+3  65+3  61+3  61+3  61+3  65+3  61+3  53+3  53+3   
2  81+3  81+3  81+3  88+3  65+3  60+3  60+3  60+3  65+3  60+3  47+3  47+3   
3   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
4  87+3  87+3  87+3  88+3  77+3  77+3  77+3  77+3  77+3  73+3  66+3  66+3   

    RCB    RB  Crossing  Finishing  HeadingAccuracy  ShortPassing  Volleys  \
0  47+2  59+2      84.0       95.0             70.0          90.0     86.0   
1  53+3  61+3      84.0       94.0             89.0          81.0     87.0   
2  47+3  60+3      79.0       87.0             62.0          84.0     84.0   
3   NaN   NaN      17.0       13.0             21.0          50.0     13.0   
4  66+3  73+3      93.0       82.0             55.0          92.0     82.0   

   Dribbling  Curve  FKAccuracy  LongPassing  BallControl  Acceleration  \
0       97.0   93.0        94.0         87.0         96.0          91.0   
1       88.0   81.0        76.0         77.0         94.0          89.0   
2       96.0   88.0        87.0         78.0         95.0          94.0   
3       18.0   21.0        19.0         51.0         42.0          57.0   
4       86.0   85.0        83.0         91.0         91.0          78.0   

   SprintSpeed  Agility  Reactions  Balance  ShotPower  Jumping  Stamina  \
0         86.0     91.0       95.0     95.0       85.0     68.0     72.0   
1         91.0     87.0       96.0     70.0       95.0     95.0     88.0   
2         90.0     96.0       94.0     84.0       80.0     61.0     81.0   
3         58.0     60.0       90.0     43.0       31.0     67.0     43.0   
4         76.0     79.0       91.0     77.0       91.0     63.0     90.0   

   Strength  LongShots  Aggression  Interceptions  Positioning  Vision  \
0      59.0       94.0        48.0           22.0         94.0    94.0   
1      79.0       93.0        63.0           29.0         95.0    82.0   
2      49.0       82.0        56.0           36.0         89.0    87.0   
3      64.0       12.0        38.0           30.0         12.0    68.0   
4      75.0       91.0        76.0           61.0      

Una vez realizado, al ver la tabla, me fijo en las columnas **Joined, Loaned From y Contract Valid until**. Esas columnas las voy a eliminar. Las dos primeras columnas mencionadas (cuando se unió al club y si está cedido) dan igual a la hora de influir en el precio de un jugador. Sé que la tercera en la vida real puede influir, pero considero que al tratarse del modo mánager de un videojuego no toma tanta importancia, así que también la elimino.

También me he decantado finalmente por eliminar **Body Type**, ya que en primera instancia pensé que podía ser importante, ya que eso puede significar que un jugador tenga las animaciones y rasgos reales del jugador que menciona el body type. Pero claro, ese aspecto solamente tiene mucha importancia en el modo Ultimate Team. En el modo de Temporada, que es en el que nos hemos centrado, realmente se le puede quitar importancia ya que los jugadores que interesan son los que tienen buen potencial y son jóvenes, y esos casi nunca tienen las animaciones y rasgos bien hechos debido a su corta trayectoria futbolística.

In [11]:
df.drop(['Joined','Loaned From','Contract Valid Until', 'Body Type'], axis = 1,inplace=True)
df.head()

Age  Overall  Potential        Value      Wage  Special  \
0   31       94         94  110500000.0  565000.0     2202   
1   33       94         94   77000000.0  405000.0     2228   
2   26       92         93  118500000.0  290000.0     2143   
3   27       91         93   72000000.0  260000.0     1471   
4   27       91         92  102000000.0  355000.0     2281   

   International Reputation  Weak Foot  Skill Moves       Work Rate Height  \
0                       5.0        4.0          4.0  Medium/ Medium    5'7   
1                       5.0        4.0          5.0       High/ Low    6'2   
2                       5.0        5.0          5.0    High/ Medium    5'9   
3                       4.0        3.0          1.0  Medium/ Medium    6'4   
4                       4.0        5.0          4.0      High/ High   5'11   

   Weight    LS    ST    RS    LW    LF    CF    RF    RW   LAM   CAM   RAM  \
0  159lbs  88+2  88+2  88+2  92+2  93+2  93+2  93+2  92+2  93+2  93+2  93+2   
1  183lbs  91+3  91+3  91+3  89+3  90+3  90+3  90+3  89+3  88+3  88+3  88+3   
2  150lbs  84+3  84+3  84+3  89+3  89+3  89+3  89+3  89+3  89+3  89+3  89+3   
3  168lbs   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
4  154lbs  82+3  82+3  82+3  87+3  87+3  87+3  87+3  87+3  88+3  88+3  88+3   

     LM   LCM    CM   RCM    RM   LWB   LDM   CDM   RDM   RWB    LB   LCB  \
0  91+2  84+2  84+2  84+2  91+2  64+2  61+2  61+2  61+2  64+2  59+2  47+2   
1  88+3  81+3  81+3  81+3  88+3  65+3  61+3  61+3  61+3  65+3  61+3  53+3   
2  88+3  81+3  81+3  81+3  88+3  65+3  60+3  60+3  60+3  65+3  60+3  47+3   
3   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
4  88+3  87+3  87+3  87+3  88+3  77+3  77+3  77+3  77+3  77+3  73+3  66+3   

     CB   RCB    RB  Crossing  Finishing  HeadingAccuracy  ShortPassing  \
0  47+2  47+2  59+2      84.0       95.0             70.0          90.0   
1  53+3  53+3  61+3      84.0       94.0             89.0          81.0   
2  47+3  47+3  60+3      79.0       87.0             62.0          84.0   
3   NaN   NaN   NaN      17.0       13.0             21.0          50.0   
4  66+3  66+3  73+3      93.0       82.0             55.0          92.0   

   Volleys  Dribbling  Curve  FKAccuracy  LongPassing  BallControl  \
0     86.0       97.0   93.0        94.0         87.0         96.0   
1     87.0       88.0   81.0        76.0         77.0         94.0   
2     84.0       96.0   88.0        87.0         78.0         95.0   
3     13.0       18.0   21.0        19.0         51.0         42.0   
4     82.0       86.0   85.0        83.0         91.0         91.0   

   Acceleration  SprintSpeed  Agility  Reactions  Balance  ShotPower  Jumping  \
0          91.0         86.0     91.0       95.0     95.0       85.0     68.0   
1          89.0         91.0     87.0       96.0     70.0       95.0     95.0   
2          94.0         90.0     96.0       94.0     84.0       80.0     61.0   
3          57.0         58.0     60.0       90.0     43.0       31.0     67.0   
4          78.0         76.0     79.0       91.0     77.0       91.0     63.0   

   Stamina  Strength  LongShots  Aggression  Interceptions  Positioning  \
0     72.0      59.0       94.0        48.0           22.0         94.0   
1     88.0      79.0       93.0        63.0           29.0         95.0   
2     81.0      49.0       82.0        56.0           36.0         89.0   
3     43.0      64.0       12.0        38.0           30.0         12.0   
4     90.0      75.0       91.0        76.0           61.0         87.0   

   Vision  Penalties  Composure  Marking  StandingTackle  SlidingTackle  \
0    94.0       75.0       96.0     33.0            28.0           26.0   
1    82.0       85.0       95.0     28.0            31.0           23.0   
2    87.0       81.0       94.0     27.0            24.0           33.0   
3    68.0       40.0       68.0     15.0            21.0           13.0   
4    94.0       79.0       88.0     68

El siguiente problema que veo es que el **Work Rate**, que es el desempeño que va a tener un jugador en **ataque** y en **defensa** (colocados en ese orden), tiene los dos valores en la misma columna. Este valor me interesa tenerlo ya que según la posición que tenga un jugador, es importante que tenga alto, medio o bajo. Por ejemplo, un defensa nos interesa que tenga alto en defensa, y un delantero alto en ataque. Un buen centrocampista "box to box" estaría asociado a tener alto y alto en las dos. ASí que primero de todo voy a **dividirlos** en dos columnas diferentes, para poder así luego realizar el correspondiente hot encoding.

In [12]:
df[['Attack Work Rate','Defense Work Rate']] = df['Work Rate'].str.split('/',n=1,expand= True)
df.pop("Work Rate")
df.head()

Age  Overall  Potential        Value      Wage  Special  \
0   31       94         94  110500000.0  565000.0     2202   
1   33       94         94   77000000.0  405000.0     2228   
2   26       92         93  118500000.0  290000.0     2143   
3   27       91         93   72000000.0  260000.0     1471   
4   27       91         92  102000000.0  355000.0     2281   

   International Reputation  Weak Foot  Skill Moves Height  Weight    LS  \
0                       5.0        4.0          4.0    5'7  159lbs  88+2   
1                       5.0        4.0          5.0    6'2  183lbs  91+3   
2                       5.0        5.0          5.0    5'9  150lbs  84+3   
3                       4.0        3.0          1.0    6'4  168lbs   NaN   
4                       4.0        5.0          4.0   5'11  154lbs  82+3   

     ST    RS    LW    LF    CF    RF    RW   LAM   CAM   RAM    LM   LCM  \
0  88+2  88+2  92+2  93+2  93+2  93+2  92+2  93+2  93+2  93+2  91+2  84+2   
1  91+3  91+3  89+3  90+3  90+3  90+3  89+3  88+3  88+3  88+3  88+3  81+3   
2  84+3  84+3  89+3  89+3  89+3  89+3  89+3  89+3  89+3  89+3  88+3  81+3   
3   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
4  82+3  82+3  87+3  87+3  87+3  87+3  87+3  88+3  88+3  88+3  88+3  87+3   

     CM   RCM    RM   LWB   LDM   CDM   RDM   RWB    LB   LCB    CB   RCB  \
0  84+2  84+2  91+2  64+2  61+2  61+2  61+2  64+2  59+2  47+2  47+2  47+2   
1  81+3  81+3  88+3  65+3  61+3  61+3  61+3  65+3  61+3  53+3  53+3  53+3   
2  81+3  81+3  88+3  65+3  60+3  60+3  60+3  65+3  60+3  47+3  47+3  47+3   
3   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
4  87+3  87+3  88+3  77+3  77+3  77+3  77+3  77+3  73+3  66+3  66+3  66+3   

     RB  Crossing  Finishing  HeadingAccuracy  ShortPassing  Volleys  \
0  59+2      84.0       95.0             70.0          90.0     86.0   
1  61+3      84.0       94.0             89.0          81.0     87.0   
2  60+3      79.0       87.0             62.0          84.0     84.0   
3   NaN      17.0       13.0             21.0          50.0     13.0   
4  73+3      93.0       82.0             55.0          92.0     82.0   

   Dribbling  Curve  FKAccuracy  LongPassing  BallControl  Acceleration  \
0       97.0   93.0        94.0         87.0         96.0          91.0   
1       88.0   81.0        76.0         77.0         94.0          89.0   
2       96.0   88.0        87.0         78.0         95.0          94.0   
3       18.0   21.0        19.0         51.0         42.0          57.0   
4       86.0   85.0        83.0         91.0         91.0          78.0   

   SprintSpeed  Agility  Reactions  Balance  ShotPower  Jumping  Stamina  \
0         86.0     91.0       95.0     95.0       85.0     68.0     72.0   
1         91.0     87.0       96.0     70.0       95.0     95.0     88.0   
2         90.0     96.0       94.0     84.0       80.0     61.0     81.0   
3         58.0     60.0       90.0     43.0       31.0     67.0     43.0   
4         76.0     79.0       91.0     77.0       91.0     63.0     90.0   

   Strength  LongShots  Aggression  Interceptions  Positioning  Vision  \
0      59.0       94.0        48.0           22.0         94.0    94.0   
1      79.0       93.0        63.0           29.0         95.0    82.0   
2      49.0       82.0        56.0           36.0         89.0    87.0   
3      64.0       12.0        38.0           30.0         12.0    68.0   
4      75.0       91.0        76.0           61.0         87.0    94.0   

   Penalties  Composure  Marking  StandingTackle  SlidingTackle  GKDiving  \
0       75.0       96.0     33.0            28.0           26.0       6.0   
1       85.0       95.0     28.0            31.0           23.0       7.0   
2       81.0       94.0     27.0            24.0           33.0       9.0   
3       40.0       68.0     15.0            21.0           13.0      90.0   
4       79.0       88.0     68.0            58.0           51.0      15.0   

Una vez ejecutado, vemos que se ha separado correctamente (están al final) y está listo para hacerle el hot encoding, que lo haré más adelante.

Ahora, un pequeño problema que nos surge ahora es que, la coma de la altura, está arriba **(')**, y nos interesa tenerlo en **float**. Así que defino una función para cambiarlo.

In [13]:
def heigh_to_float(x):
    """
    x'x -> x.x
    """
    x = x.split("'")
    
    if(len(x[1])==1): x = float(x[0]) + float(x[1])/10
    else:
        y = float(x[1])
        y = y/100
        x = float(x[0])+y

    return x

> He intentado aplicar la función, pero creo que hay jugadores con NaN en la altura, ya que nos ha saltado un error. Lo comprobamos a continuación, ejecutando una instrucción para ver si hay NaNs en dicha columna:

In [14]:
df.loc[df['Height'].isnull()]

Age  Overall  Potential     Value    Wage  Special  \
13236   33       62         62  120000.0  1000.0     1510   
13237   29       62         62  300000.0  1000.0     1532   
13238   35       62         62  140000.0  3000.0     1573   
13239   20       62         72  425000.0  1000.0     1610   
13240   24       62         66  400000.0  1000.0     1481   
13241   21       62         72  425000.0  1000.0     1692   
13242   23       62         70  450000.0  2000.0     1663   
13243   19       62         78  600000.0  5000.0     1328   
13244   30       62         62  230000.0  2000.0     1244   
13245   21       62         69  425000.0  1000.0     1549   
13246   22       62         68  425000.0  2000.0     1494   
13247   28       62         62  240000.0  3000.0     1630   
13248   24       62         69  375000.0  2000.0     1461   
13249   27       62         62  250000.0  3000.0     1636   
13250   29       62         62  300000.0  1000.0     1454   
13251   34       62         62  150000.0  2000.0     1665   
13252   22       62         70  375000.0  1000.0     1587   
13253   31       62         62  200000.0  2000.0     1535   
13254   17       62         82  550000.0  2000.0     1418   
13255   25       62         65  325000.0  1000.0     1693   
13256   26       62         62  325000.0  1000.0     1712   
13257   25       62         65  375000.0  2000.0     1536   
13258   23       62         67  350000.0  3000.0     1664   
13259   27       62         65  300000.0  1000.0     1316   
13260   20       62         69  425000.0  1000.0     1574   
13261   25       62         64  300000.0  5000.0     1665   
13262   24       62         66  325000.0  1000.0     1625   
13263   25       62         66  325000.0  2000.0     1354   
13264   29       62         62  300000.0  1000.0     1620   
13265   28       62         62  300000.0  3000.0     1740   
13266   20       62         73  525000.0  1000.0     1549   
13267   22       62         70  450000.0  1000.0     1607   
13268   37       62         62  100000.0  1000.0     1542   
13269   26       62         64  375000.0  1000.0     1552   
13270   19       62         77  525000.0  1000.0     1141   
13271   26       62         63  290000.0  1000.0     1497   
13272   22       62         70  450000.0  1000.0     1614   
13273   25       62         67  400000.0  1000.0     1686   
13274   27       62         62  325000.0  2000.0     1670   
13275   23       62         70  375000.0  1000.0     1542   
13276   26       62         63  290000.0  3000.0     1679   
13277   26       62         62  325000.0  1000.0     1675   
13278   17       62         79  550000.0  1000.0     1545   
13279   22       62         69  350000.0  1000.0     1681   
13280   19       62         77  650000.0  2000.0     1478   
13281   27       62         62  300000.0  1000.0     1729   
13282   25       62         65  375000.0  2000.0     1661   
13283   25       62         66  325000.0  2000.0     1578   

       International Reputation  Weak Foot  Skill Moves Height Weight   LS  \
13236                       NaN        NaN          NaN    NaN    NaN  NaN   
13237                       NaN        NaN          NaN    NaN    NaN  NaN   
13238                       NaN        NaN          NaN    NaN    NaN  NaN   
13239                       NaN        NaN          NaN    NaN    NaN  NaN   
13240                       NaN        NaN          NaN    NaN    NaN  NaN   
13241                       NaN        NaN          NaN    NaN    NaN  NaN   
13242                       NaN        NaN          NaN    NaN    NaN  NaN   
13243                       NaN        NaN          NaN    NaN    NaN  NaN   
13244                       NaN        NaN          NaN    NaN    NaN  NaN   
13245                       NaN        NaN          NaN    NaN    NaN  NaN   
13246                       NaN        NaN          NaN    NaN    NaN  NaN   
13247                       NaN        NaN          NaN    NaN    NaN  NaN   
132

Una vez ejecutada, vemos que nuestra suposición era cierta, lo que viene con la "sorpresa" de que no solo tienen la altura en NaN, sino que tienen todos los atributos en ``NaN``. Podemos ver que hay **47 jugadores** en total, que para este caso nos son *inútiles* a la hora de entrenar al modelo, así que los voy a eliminar todos.
Para ello, aplicaré la siguiente instrucción, que eliminará los valores que tienen NaN en la altura, ya que hemos visto que si tienen NaN en la altura, todo lo demás también. Así que simplemente eliminandolos se arregla el problema.

In [15]:
df = df.dropna(subset = ['Height'])

>Una vez ejecutada la instrucción anterior, ahora sí que está listo para aplicarle la función en la altura para pasar ese número a float. 

Aplicamos la función y de paso vemos la cabecera de la tabla para comprobar que se ha cambiado correctamente:

In [16]:
df["Height"] = df["Height"].apply(heigh_to_float)
df.head()

Age  Overall  Potential        Value      Wage  Special  \
0   31       94         94  110500000.0  565000.0     2202   
1   33       94         94   77000000.0  405000.0     2228   
2   26       92         93  118500000.0  290000.0     2143   
3   27       91         93   72000000.0  260000.0     1471   
4   27       91         92  102000000.0  355000.0     2281   

   International Reputation  Weak Foot  Skill Moves  Height  Weight    LS  \
0                       5.0        4.0          4.0    5.70  159lbs  88+2   
1                       5.0        4.0          5.0    6.20  183lbs  91+3   
2                       5.0        5.0          5.0    5.90  150lbs  84+3   
3                       4.0        3.0          1.0    6.40  168lbs   NaN   
4                       4.0        5.0          4.0    5.11  154lbs  82+3   

     ST    RS    LW    LF    CF    RF    RW   LAM   CAM   RAM    LM   LCM  \
0  88+2  88+2  92+2  93+2  93+2  93+2  92+2  93+2  93+2  93+2  91+2  84+2   
1  91+3  91+3  89+3  90+3  90+3  90+3  89+3  88+3  88+3  88+3  88+3  81+3   
2  84+3  84+3  89+3  89+3  89+3  89+3  89+3  89+3  89+3  89+3  88+3  81+3   
3   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
4  82+3  82+3  87+3  87+3  87+3  87+3  87+3  88+3  88+3  88+3  88+3  87+3   

     CM   RCM    RM   LWB   LDM   CDM   RDM   RWB    LB   LCB    CB   RCB  \
0  84+2  84+2  91+2  64+2  61+2  61+2  61+2  64+2  59+2  47+2  47+2  47+2   
1  81+3  81+3  88+3  65+3  61+3  61+3  61+3  65+3  61+3  53+3  53+3  53+3   
2  81+3  81+3  88+3  65+3  60+3  60+3  60+3  65+3  60+3  47+3  47+3  47+3   
3   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
4  87+3  87+3  88+3  77+3  77+3  77+3  77+3  77+3  73+3  66+3  66+3  66+3   

     RB  Crossing  Finishing  HeadingAccuracy  ShortPassing  Volleys  \
0  59+2      84.0       95.0             70.0          90.0     86.0   
1  61+3      84.0       94.0             89.0          81.0     87.0   
2  60+3      79.0       87.0             62.0          84.0     84.0   
3   NaN      17.0       13.0             21.0          50.0     13.0   
4  73+3      93.0       82.0             55.0          92.0     82.0   

   Dribbling  Curve  FKAccuracy  LongPassing  BallControl  Acceleration  \
0       97.0   93.0        94.0         87.0         96.0          91.0   
1       88.0   81.0        76.0         77.0         94.0          89.0   
2       96.0   88.0        87.0         78.0         95.0          94.0   
3       18.0   21.0        19.0         51.0         42.0          57.0   
4       86.0   85.0        83.0         91.0         91.0          78.0   

   SprintSpeed  Agility  Reactions  Balance  ShotPower  Jumping  Stamina  \
0         86.0     91.0       95.0     95.0       85.0     68.0     72.0   
1         91.0     87.0       96.0     70.0       95.0     95.0     88.0   
2         90.0     96.0       94.0     84.0       80.0     61.0     81.0   
3         58.0     60.0       90.0     43.0       31.0     67.0     43.0   
4         76.0     79.0       91.0     77.0       91.0     63.0     90.0   

   Strength  LongShots  Aggression  Interceptions  Positioning  Vision  \
0      59.0       94.0        48.0           22.0         94.0    94.0   
1      79.0       93.0        63.0           29.0         95.0    82.0   
2      49.0       82.0        56.0           36.0         89.0    87.0   
3      64.0       12.0        38.0           30.0         12.0    68.0   
4      75.0       91.0        76.0           61.0         87.0    94.0   

   Penalties  Composure  Marking  StandingTackle  SlidingTackle  GKDiving  \
0       75.0       96.0     33.0            28.0           26.0       6.0   
1       85.0       95.0     28.0            31.0           23.0       7.0   
2       81.0       94.0     27.0            24.0           33.0       9.0   
3       40.0       68.0     15.0            21.0           13.0      90.0   
4       79.0       88.0     68.0            58.0           51.0      1

Efectivamente, ha funcionado de la manera esperada y ahora sí que está listo para ser tratado correctamente.

Ahora haré lo propio con el Peso del jugador, ya que contiene *lbs*, que nos molesta en el algoritmo.
Eliminamos **lbs** (libras) del **Weight** (peso) del jugador.
> Primero, definimos la función que complace lo que queremos hacer.

In [17]:
def weight_to_float(x):
    """
    From lbs to float.
    
    """
    if 'lbs' in x:
            ret_val = float(x.replace('lbs', ''))
    return ret_val

Una vez definida, la aplico en la columna de peso del jugador para eliminar lbs y que se quede guardado en float.

In [18]:
df["Weight"] = df["Weight"].apply(weight_to_float)
df.head()

Age  Overall  Potential        Value      Wage  Special  \
0   31       94         94  110500000.0  565000.0     2202   
1   33       94         94   77000000.0  405000.0     2228   
2   26       92         93  118500000.0  290000.0     2143   
3   27       91         93   72000000.0  260000.0     1471   
4   27       91         92  102000000.0  355000.0     2281   

   International Reputation  Weak Foot  Skill Moves  Height  Weight    LS  \
0                       5.0        4.0          4.0    5.70   159.0  88+2   
1                       5.0        4.0          5.0    6.20   183.0  91+3   
2                       5.0        5.0          5.0    5.90   150.0  84+3   
3                       4.0        3.0          1.0    6.40   168.0   NaN   
4                       4.0        5.0          4.0    5.11   154.0  82+3   

     ST    RS    LW    LF    CF    RF    RW   LAM   CAM   RAM    LM   LCM  \
0  88+2  88+2  92+2  93+2  93+2  93+2  92+2  93+2  93+2  93+2  91+2  84+2   
1  91+3  91+3  89+3  90+3  90+3  90+3  89+3  88+3  88+3  88+3  88+3  81+3   
2  84+3  84+3  89+3  89+3  89+3  89+3  89+3  89+3  89+3  89+3  88+3  81+3   
3   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
4  82+3  82+3  87+3  87+3  87+3  87+3  87+3  88+3  88+3  88+3  88+3  87+3   

     CM   RCM    RM   LWB   LDM   CDM   RDM   RWB    LB   LCB    CB   RCB  \
0  84+2  84+2  91+2  64+2  61+2  61+2  61+2  64+2  59+2  47+2  47+2  47+2   
1  81+3  81+3  88+3  65+3  61+3  61+3  61+3  65+3  61+3  53+3  53+3  53+3   
2  81+3  81+3  88+3  65+3  60+3  60+3  60+3  65+3  60+3  47+3  47+3  47+3   
3   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
4  87+3  87+3  88+3  77+3  77+3  77+3  77+3  77+3  73+3  66+3  66+3  66+3   

     RB  Crossing  Finishing  HeadingAccuracy  ShortPassing  Volleys  \
0  59+2      84.0       95.0             70.0          90.0     86.0   
1  61+3      84.0       94.0             89.0          81.0     87.0   
2  60+3      79.0       87.0             62.0          84.0     84.0   
3   NaN      17.0       13.0             21.0          50.0     13.0   
4  73+3      93.0       82.0             55.0          92.0     82.0   

   Dribbling  Curve  FKAccuracy  LongPassing  BallControl  Acceleration  \
0       97.0   93.0        94.0         87.0         96.0          91.0   
1       88.0   81.0        76.0         77.0         94.0          89.0   
2       96.0   88.0        87.0         78.0         95.0          94.0   
3       18.0   21.0        19.0         51.0         42.0          57.0   
4       86.0   85.0        83.0         91.0         91.0          78.0   

   SprintSpeed  Agility  Reactions  Balance  ShotPower  Jumping  Stamina  \
0         86.0     91.0       95.0     95.0       85.0     68.0     72.0   
1         91.0     87.0       96.0     70.0       95.0     95.0     88.0   
2         90.0     96.0       94.0     84.0       80.0     61.0     81.0   
3         58.0     60.0       90.0     43.0       31.0     67.0     43.0   
4         76.0     79.0       91.0     77.0       91.0     63.0     90.0   

   Strength  LongShots  Aggression  Interceptions  Positioning  Vision  \
0      59.0       94.0        48.0           22.0         94.0    94.0   
1      79.0       93.0        63.0           29.0         95.0    82.0   
2      49.0       82.0        56.0           36.0         89.0    87.0   
3      64.0       12.0        38.0           30.0         12.0    68.0   
4      75.0       91.0        76.0           61.0         87.0    94.0   

   Penalties  Composure  Marking  StandingTackle  SlidingTackle  GKDiving  \
0       75.0       96.0     33.0            28.0           26.0       6.0   
1       85.0       95.0     28.0            31.0           23.0       7.0   
2       81.0       94.0     27.0            24.0           33.0       9.0   
3       40.0       68.0     15.0            21.0           13.0      90.0   
4       79.0       88.0     68.0            58.0           51.0      1

Vemos que ha ido correctamente y salen ya el peso y la altura debidamente en float.

Ahora, lo que quiero arreglar son las columnas de rendimiento del jugador en cada **posición** (LS,ST,RS,etc.), ya que tienen una suma de dos números. He pensado que sería mejor tener simplemente el resultado de esa suma en float. Para ello 
definiré una fórmula para **sumar** los valores y que quede en un **único valor** numérico.
>Los ``NaN`` los dejamos como están y los gestionaré a continuación.

In [19]:
def add_pos(x):
    """
    Se suman los valores de la posición. 
    
    """
    
    if(x != x): return np.nan
    
    values = x.split('+')
    
    return (float(values[0])+float(values[1]))

Una vez definida la función, la aplico en cada columna que sea una posición de campo. Para no tener que hacerlo linea por linea, creo un **array** con todas las columnas donde me interesa aplicarla y hago un **for** que la aplique columna por columna.

In [20]:
posiciones = ["LS","ST","RS","LW","LF","CF","RF","RW","LAM","CAM","RAM","LM","LCM","CM","RCM","RM","LWB","LDM","CDM","RDM","RWB","LB","LCB","CB","RCB","RB"]
for i in posiciones: df[i]=df[i].apply(add_pos)

In [21]:
df.head()

Age  Overall  Potential        Value      Wage  Special  \
0   31       94         94  110500000.0  565000.0     2202   
1   33       94         94   77000000.0  405000.0     2228   
2   26       92         93  118500000.0  290000.0     2143   
3   27       91         93   72000000.0  260000.0     1471   
4   27       91         92  102000000.0  355000.0     2281   

   International Reputation  Weak Foot  Skill Moves  Height  Weight    LS  \
0                       5.0        4.0          4.0    5.70   159.0  90.0   
1                       5.0        4.0          5.0    6.20   183.0  94.0   
2                       5.0        5.0          5.0    5.90   150.0  87.0   
3                       4.0        3.0          1.0    6.40   168.0   NaN   
4                       4.0        5.0          4.0    5.11   154.0  85.0   

     ST    RS    LW    LF    CF    RF    RW   LAM   CAM   RAM    LM   LCM  \
0  90.0  90.0  94.0  95.0  95.0  95.0  94.0  95.0  95.0  95.0  93.0  86.0   
1  94.0  94.0  92.0  93.0  93.0  93.0  92.0  91.0  91.0  91.0  91.0  84.0   
2  87.0  87.0  92.0  92.0  92.0  92.0  92.0  92.0  92.0  92.0  91.0  84.0   
3   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
4  85.0  85.0  90.0  90.0  90.0  90.0  90.0  91.0  91.0  91.0  91.0  90.0   

     CM   RCM    RM   LWB   LDM   CDM   RDM   RWB    LB   LCB    CB   RCB  \
0  86.0  86.0  93.0  66.0  63.0  63.0  63.0  66.0  61.0  49.0  49.0  49.0   
1  84.0  84.0  91.0  68.0  64.0  64.0  64.0  68.0  64.0  56.0  56.0  56.0   
2  84.0  84.0  91.0  68.0  63.0  63.0  63.0  68.0  63.0  50.0  50.0  50.0   
3   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
4  90.0  90.0  91.0  80.0  80.0  80.0  80.0  80.0  76.0  69.0  69.0  69.0   

     RB  Crossing  Finishing  HeadingAccuracy  ShortPassing  Volleys  \
0  61.0      84.0       95.0             70.0          90.0     86.0   
1  64.0      84.0       94.0             89.0          81.0     87.0   
2  63.0      79.0       87.0             62.0          84.0     84.0   
3   NaN      17.0       13.0             21.0          50.0     13.0   
4  76.0      93.0       82.0             55.0          92.0     82.0   

   Dribbling  Curve  FKAccuracy  LongPassing  BallControl  Acceleration  \
0       97.0   93.0        94.0         87.0         96.0          91.0   
1       88.0   81.0        76.0         77.0         94.0          89.0   
2       96.0   88.0        87.0         78.0         95.0          94.0   
3       18.0   21.0        19.0         51.0         42.0          57.0   
4       86.0   85.0        83.0         91.0         91.0          78.0   

   SprintSpeed  Agility  Reactions  Balance  ShotPower  Jumping  Stamina  \
0         86.0     91.0       95.0     95.0       85.0     68.0     72.0   
1         91.0     87.0       96.0     70.0       95.0     95.0     88.0   
2         90.0     96.0       94.0     84.0       80.0     61.0     81.0   
3         58.0     60.0       90.0     43.0       31.0     67.0     43.0   
4         76.0     79.0       91.0     77.0       91.0     63.0     90.0   

   Strength  LongShots  Aggression  Interceptions  Positioning  Vision  \
0      59.0       94.0        48.0           22.0         94.0    94.0   
1      79.0       93.0        63.0           29.0         95.0    82.0   
2      49.0       82.0        56.0           36.0         89.0    87.0   
3      64.0       12.0        38.0           30.0         12.0    68.0   
4      75.0       91.0        76.0           61.0         87.0    94.0   

   Penalties  Composure  Marking  StandingTackle  SlidingTackle  GKDiving  \
0       75.0       96.0     33.0            28.0           26.0       6.0   
1       85.0       95.0     28.0            31.0           23.0       7.0   
2       81.0       94.0     27.0            24.0           33.0       9.0   
3       40.0       68.0     15.0            21.0           13.0      90.0   
4       79.0       88.0     68.0            58.0           51.0      1

Vemos que ha funcionado correctamente. Ahora todas las posiciones tienen el resultado de la suma de los dos números que tenían y estan en float.

## Gestión de los porteros
Una vez hecho lo anterior, me topo con el problema de que tienen ``NaN`` en **todas** las posiciones de campo, y no nos interesa que pase eso. Por tanto, para gestionar el problema de los NaN en los porteros, se me ha ocurrido hacer la **media** de todos los valores de una columna y ponerla en los porteros. Así no tendrán NaNs y podremos tenerlos en cuenta para el algoritmo. Esta media no será muy alta ya que aunque haya jugadores muy top, también hay jugadores muy malos, así que nos quedarán con un número aceptable tirando a malo. 
Así conseguiremos un tratamiento justo para un jugador que juegue de portero.
> Encuentro que esto es más justo que ponerles un 0 a todos ellos en cada posición, y obviamente mucho mejor que eliminarlos.


Antes de hacer la media, quiero comprobar dos cosas:

    1: Ver si realmente los que tienen NaN en las posiciones LS, ST, etc. son realmente porteros o tenemos jugadores como el caso que nos ha pasado antes, que era inútil mantenerlos en la base de datos.
    2: Ejecutar una instrucción que nos diga si queda algun NaN en otra columna por si se nos ha escapado anteriormente.

In [22]:
df.loc[df['ST'].isnull()]

Age  Overall  Potential       Value      Wage  Special  \
3       27       91         93  72000000.0  260000.0     1471   
9       25       90         93  68000000.0   94000.0     1331   
18      26       89         92  58000000.0  240000.0     1328   
19      26       89         90  53500000.0  240000.0     1311   
22      32       89         89  38000000.0  130000.0     1473   
...    ...      ...        ...         ...       ...      ...   
18178   18       48         65     50000.0    1000.0      738   
18180   22       48         58     40000.0    1000.0      987   
18183   44       48         48         0.0    1000.0      774   
18194   18       47         65     50000.0    1000.0      731   
18198   18       47         70     60000.0    1000.0      792   

       International Reputation  Weak Foot  Skill Moves  Height  Weight  LS  \
3                           4.0        3.0          1.0    6.40   168.0 NaN   
9                           3.0        3.0          1.0    6.20   192.0 NaN   
18                          3.0        4.0          1.0    6.20   187.0 NaN   
19                          4.0        2.0          1.0    6.60   212.0 NaN   
22                          5.0        4.0          1.0    6.40   203.0 NaN   
...                         ...        ...          ...     ...     ...  ..   
18178                       1.0        2.0          1.0    6.00   176.0 NaN   
18180                       1.0        2.0          1.0    6.10   172.0 NaN   
18183                       1.0        2.0          1.0    6.20   190.0 NaN   
18194                       1.0        3.0          1.0    6.30   187.0 NaN   
18198                       1.0        2.0          1.0    5.11   154.0 NaN   

       ST  RS  LW  LF  CF  RF  RW  LAM  CAM  RAM  LM  LCM  CM  RCM  RM  LWB  \
3     NaN NaN NaN NaN NaN NaN NaN  NaN  NaN  NaN NaN  NaN NaN  NaN NaN  NaN   
9     NaN NaN NaN NaN NaN NaN NaN  NaN  NaN  NaN NaN  NaN NaN  NaN NaN  NaN   
18    NaN NaN NaN NaN NaN NaN NaN  NaN  NaN  NaN NaN  NaN NaN  NaN NaN  NaN   
19    NaN NaN NaN NaN NaN NaN NaN  NaN  NaN  NaN NaN  NaN NaN  NaN NaN  NaN   
22    NaN NaN NaN NaN NaN NaN NaN  NaN  NaN  NaN NaN  NaN NaN  NaN NaN  NaN   
...    ..  ..  ..  ..  ..  ..  ..  ...  ...  ...  ..  ...  ..  ...  ..  ...   
18178 NaN NaN NaN NaN NaN NaN NaN  NaN  NaN  NaN NaN  NaN NaN  NaN NaN  NaN   
18180 NaN NaN NaN NaN NaN NaN NaN  NaN  NaN  NaN NaN  NaN NaN  NaN NaN  NaN   
18183 NaN NaN NaN NaN NaN NaN NaN  NaN  NaN  NaN NaN  NaN NaN  NaN NaN  NaN   
18194 NaN NaN NaN NaN NaN NaN NaN  NaN  NaN  NaN NaN  NaN NaN  NaN NaN  NaN   
18198 NaN NaN NaN NaN NaN NaN NaN  NaN  NaN  NaN NaN  NaN NaN  NaN NaN  NaN   

       LDM  CDM  RDM  RWB  LB  LCB  CB  RCB  RB  Crossing  Finishing  \
3      NaN  NaN  NaN  NaN NaN  NaN NaN  NaN NaN      17.0       13.0   
9      NaN  NaN  NaN  NaN NaN  NaN NaN  NaN NaN      13.0       11.0   
18     NaN  NaN  NaN  NaN NaN  NaN NaN  NaN NaN      15.0       14.0   
19     NaN  NaN  NaN  NaN NaN  NaN NaN  NaN NaN      14.0       14.0   
22     NaN  NaN  NaN  NaN NaN  NaN NaN  NaN NaN      15.0       13.0   
...    ...  ...  ...  ...  ..  ...  ..  ...  ..       ...        ...   
18178  NaN  NaN  NaN  NaN NaN  NaN NaN  NaN NaN      10.0        7.0   
18180  NaN  NaN  NaN  NaN NaN  NaN NaN  NaN NaN      19.0       15.0   
18183  NaN  NaN  NaN  NaN NaN  NaN NaN  NaN NaN      11.0       12.0   
18194  NaN  NaN  NaN  NaN NaN  NaN NaN  NaN NaN      10.0        6.0   
18198  NaN  NaN  NaN  NaN NaN  NaN NaN  NaN NaN      14.0        8.0   

       HeadingAccuracy  ShortPassing  Volleys  Dribbling  Curve  FKAccuracy  \
3                 21.0          50.0     13.0       18.0   21.0        19.0   
9                 15.0          29.0     13.0       12.0   13.0        14.0   
18                11.0          36.0     14.0       17.0   18.0        12.0   
19                13.0          33.0     12.0       13.0   19.0        20.0   
22                25.0          55.0     11.0       30.0   14.0     

Vemos que parece que está todo correcto, ya que todos tienen un 1 en la columna pos_GK. Eso significa que exactamente, nos quedan solo los porteros con NaN. De todas formas ejecuto por seguridad una instrucción que me diga las columnas que tienen NaN, por si acaso se me escapa alguna.

In [23]:
df.columns[df.isna().any()].tolist()

['LS',
 'ST',
 'RS',
 'LW',
 'LF',
 'CF',
 'RF',
 'RW',
 'LAM',
 'CAM',
 'RAM',
 'LM',
 'LCM',
 'CM',
 'RCM',
 'RM',
 'LWB',
 'LDM',
 'CDM',
 'RDM',
 'RWB',
 'LB',
 'LCB',
 'CB',
 'RCB',
 'RB']

Ahora sí, estoy seguro de que solo quedan los porteros con NaN, así que calculo la media de cada columna de posición y la introduzco en las filas que contienen NaN (los porteros).

In [24]:
df.fillna(df.mean(), inplace=True)
df.head()

Age  Overall  Potential        Value      Wage  Special  \
0   31       94         94  110500000.0  565000.0     2202   
1   33       94         94   77000000.0  405000.0     2228   
2   26       92         93  118500000.0  290000.0     2143   
3   27       91         93   72000000.0  260000.0     1471   
4   27       91         92  102000000.0  355000.0     2281   

   International Reputation  Weak Foot  Skill Moves  Height  Weight      LS  \
0                       5.0        4.0          4.0    5.70   159.0  90.000   
1                       5.0        4.0          5.0    6.20   183.0  94.000   
2                       5.0        5.0          5.0    5.90   150.0  87.000   
3                       4.0        3.0          1.0    6.40   168.0  59.836   
4                       4.0        5.0          4.0    5.11   154.0  85.000   

       ST      RS         LW         LF         CF         RF         RW  \
0  90.000  90.000  94.000000  95.000000  95.000000  95.000000  94.000000   
1  94.000  94.000  92.000000  93.000000  93.000000  93.000000  92.000000   
2  87.000  87.000  92.000000  92.000000  92.000000  92.000000  92.000000   
3  59.836  59.836  61.058181  60.739921  60.739921  60.739921  61.058181   
4  85.000  85.000  90.000000  90.000000  90.000000  90.000000  90.000000   

        LAM       CAM       RAM         LM        LCM         CM        RCM  \
0  95.00000  95.00000  95.00000  93.000000  86.000000  86.000000  86.000000   
1  91.00000  91.00000  91.00000  91.000000  84.000000  84.000000  84.000000   
2  92.00000  92.00000  92.00000  91.000000  84.000000  84.000000  84.000000   
3  61.00366  61.00366  61.00366  61.755241  60.241409  60.241409  60.241409   
4  91.00000  91.00000  91.00000  91.000000  90.000000  90.000000  90.000000   

          RM        LWB        LDM        CDM        RDM        RWB  \
0  93.000000  66.000000  63.000000  63.000000  63.000000  66.000000   
1  91.000000  68.000000  64.000000  64.000000  64.000000  68.000000   
2  91.000000  68.000000  63.000000  63.000000  63.000000  68.000000   
3  61.755241  59.533805  58.845677  58.845677  58.845677  59.533805   
4  91.000000  80.000000  80.000000  80.000000  80.000000  80.000000   

          LB        LCB         CB        RCB         RB  Crossing  Finishing  \
0  61.000000  49.000000  49.000000  49.000000  61.000000      84.0       95.0   
1  64.000000  56.000000  56.000000  56.000000  64.000000      84.0       94.0   
2  63.000000  50.000000  50.000000  50.000000  63.000000      79.0       87.0   
3  58.827317  57.635157  57.635157  57.635157  58.827317      17.0       13.0   
4  76.000000  69.000000  69.000000  69.000000  76.000000      93.0       82.0   

   HeadingAccuracy  ShortPassing  Volleys  Dribbling  Curve  FKAccuracy  \
0             70.0          90.0     86.0       97.0   93.0        94.0   
1             89.0          81.0     87.0       88.0   81.0        76.0   
2             62.0          84.0     84.0       96.0   88.0        87.0   
3             21.0          50.0     13.0       18.0   21.0        19.0   
4             55.0          92.0     82.0       86.0   85.0        83.0   

   LongPassing  BallControl  Acceleration  SprintSpeed  Agility  Reactions  \
0         87.0         96.0          91.0         86.0     91.0       95.0   
1         77.0         94.0          89.0         91.0     87.0       96.0   
2         78.0         95.0          94.0         90.0     96.0       94.0   
3         51.0         42.0          57.0         58.0     60.0       90.0   
4         91.0         91.0          78.0         76.0     79.0       91.0   

   Balance  ShotPower  Jumping  Stamina  Strength  LongShots  Aggression  \
0     95.0       85.0     68.0     72.0      59.0       94.0        48.0   
1     70.0       95.0     95.0     88.0      79.0       93.0        63.0   
2     84.0       80.0     61.0     81.0      49.0       82.0        56.0   
3     43.0       31.0     67.0     43.0      64.0       12.0        38.0   
4     77.

Una vez ejecutado, vemos que ha funcionado correctamente y en cada posición NaN que tenian los porteros, ha puesto la media de la columna. Vemos que tiene un valor de unos 58/60 puntos, que seria una carta de bronce, es decir, bastante malo. Esto me parece correcto, ya que los porteros suelen ser malos jugando en posiciones de campo (así como pasaría si pones a un jugador de campo en la portería).

Por último, pero no menos importante, voy a pasar a **Hot-Encoding** las columnas de **Attack Work Rate** y **Defense Work Rate**.

In [25]:
aw = df.pop("Attack Work Rate")
df = pd.concat([df.reset_index(drop=True), pd.get_dummies(aw, prefix='AWR').reset_index(drop=True)],axis=1, sort=False)
filtro_Pos = [col for col in df if col.startswith('AWR')]
df.drop(columns=filtro_Pos)

dw = df.pop("Defense Work Rate")
df = pd.concat([df.reset_index(drop=True), pd.get_dummies(dw, prefix='DWR').reset_index(drop=True)],axis=1, sort=False)
filtro_Pos = [col for col in df if col.startswith('DWR')]
df.drop(columns=filtro_Pos)
df.head()

Age  Overall  Potential        Value      Wage  Special  \
0   31       94         94  110500000.0  565000.0     2202   
1   33       94         94   77000000.0  405000.0     2228   
2   26       92         93  118500000.0  290000.0     2143   
3   27       91         93   72000000.0  260000.0     1471   
4   27       91         92  102000000.0  355000.0     2281   

   International Reputation  Weak Foot  Skill Moves  Height  Weight      LS  \
0                       5.0        4.0          4.0    5.70   159.0  90.000   
1                       5.0        4.0          5.0    6.20   183.0  94.000   
2                       5.0        5.0          5.0    5.90   150.0  87.000   
3                       4.0        3.0          1.0    6.40   168.0  59.836   
4                       4.0        5.0          4.0    5.11   154.0  85.000   

       ST      RS         LW         LF         CF         RF         RW  \
0  90.000  90.000  94.000000  95.000000  95.000000  95.000000  94.000000   
1  94.000  94.000  92.000000  93.000000  93.000000  93.000000  92.000000   
2  87.000  87.000  92.000000  92.000000  92.000000  92.000000  92.000000   
3  59.836  59.836  61.058181  60.739921  60.739921  60.739921  61.058181   
4  85.000  85.000  90.000000  90.000000  90.000000  90.000000  90.000000   

        LAM       CAM       RAM         LM        LCM         CM        RCM  \
0  95.00000  95.00000  95.00000  93.000000  86.000000  86.000000  86.000000   
1  91.00000  91.00000  91.00000  91.000000  84.000000  84.000000  84.000000   
2  92.00000  92.00000  92.00000  91.000000  84.000000  84.000000  84.000000   
3  61.00366  61.00366  61.00366  61.755241  60.241409  60.241409  60.241409   
4  91.00000  91.00000  91.00000  91.000000  90.000000  90.000000  90.000000   

          RM        LWB        LDM        CDM        RDM        RWB  \
0  93.000000  66.000000  63.000000  63.000000  63.000000  66.000000   
1  91.000000  68.000000  64.000000  64.000000  64.000000  68.000000   
2  91.000000  68.000000  63.000000  63.000000  63.000000  68.000000   
3  61.755241  59.533805  58.845677  58.845677  58.845677  59.533805   
4  91.000000  80.000000  80.000000  80.000000  80.000000  80.000000   

          LB        LCB         CB        RCB         RB  Crossing  Finishing  \
0  61.000000  49.000000  49.000000  49.000000  61.000000      84.0       95.0   
1  64.000000  56.000000  56.000000  56.000000  64.000000      84.0       94.0   
2  63.000000  50.000000  50.000000  50.000000  63.000000      79.0       87.0   
3  58.827317  57.635157  57.635157  57.635157  58.827317      17.0       13.0   
4  76.000000  69.000000  69.000000  69.000000  76.000000      93.0       82.0   

   HeadingAccuracy  ShortPassing  Volleys  Dribbling  Curve  FKAccuracy  \
0             70.0          90.0     86.0       97.0   93.0        94.0   
1             89.0          81.0     87.0       88.0   81.0        76.0   
2             62.0          84.0     84.0       96.0   88.0        87.0   
3             21.0          50.0     13.0       18.0   21.0        19.0   
4             55.0          92.0     82.0       86.0   85.0        83.0   

   LongPassing  BallControl  Acceleration  SprintSpeed  Agility  Reactions  \
0         87.0         96.0          91.0         86.0     91.0       95.0   
1         77.0         94.0          89.0         91.0     87.0       96.0   
2         78.0         95.0          94.0         90.0     96.0       94.0   
3         51.0         42.0          57.0         58.0     60.0       90.0   
4         91.0         91.0          78.0         76.0     79.0       91.0   

   Balance  ShotPower  Jumping  Stamina  Strength  LongShots  Aggression  \
0     95.0       85.0     68.0     72.0      59.0       94.0        48.0   
1     70.0       95.0     95.0     88.0      79.0       93.0        63.0   
2     84.0       80.0     61.0     81.0      49.0       82.0        56.0   
3     43.0       31.0     67.0     43.0      64.0       12.0        38.0   
4     77.

Podemos observar que ahora los jugadores tendrán un 1 en la columna que les corresponde de desempeño de ataque y defensa, y un 0 en las que no. 

Una vez hecho todo esto, creo que ya podemos ir a ver si funciona bien y hacer una predicción de la columna Value con la tabla que hemos preparado.

## Predicción del precio
Finalmente, queremos intentar predecir el **valor** de un jugador. Para ello, anteriormente he **modificado** la tabla, dejándola con los valores que he considerado más **adecuados**. También es importante que todos ellos estén en **valor numérico**.

Ahora, usaré esos datos para **entrenar el modelo**. 

Primero de todo, dividiremos los datos para ser capaces de conocer su **rendimiento real**.

In [26]:
val = df.pop("Value")

In [27]:
X_train, X_test, y_train, y_test = train_test_split(df, val, test_size=0.25, random_state=42)

In [28]:
len(X_train)

13619

Ahora, entrenamos el modelo de **regresión lineal**.

In [29]:
reg = linear_model.LinearRegression().fit(X_train, y_train)

Conseguimos una métrica $R^2$ para la regresion, y usamos la implementación de <a href="https://scikit-learn.org/stable/modules/generated/sklearn.metrics.r2_score.html"> sickit-learn</a>.

In [30]:
preds = reg.predict(X_test)

In [31]:
preds[0]

662993.5027522803

In [32]:
y_test[0]

110500000.0

In [33]:
r2_score(preds, y_test)

0.9660097208916449

Obtenemos un ``0'96`` sobre ``1``, lo cual no está nada mal y nos dará un resultado bastante **preciso y real** del precio de un jugador de FIFA 18.

Aquí dejo el enlace a mi repositorio: https://github.com/pedrofont11/Practica3IA